# Creating the Political Alignment Index and Merging the Datasets 

First we need to import the following packages to make everything function properly

In [1]:
import requests
import pandas as pd
import matplotlib.pyplot as plt
import numpy as np
import re
import statsmodels.api as sm
from scipy import stats
import pylab 

pylab.rcParams['figure.figsize'] = (10., 8.) 

/home/nbuser/anaconda3_501/lib/python3.6/site-packages/statsmodels/compat/pandas.py:56: FutureWarning: The pandas.core.datetools module is deprecated and will be removed in a future version. Please use the pandas.tseries module instead.
  from pandas.core import datetools


## Importing the Election Results Data

Now we need to import the election result data. There were 2 datasets for this, one ranging from 1980-2008 and one for the two most recent elections (2012 and 2016). The 'Outcome' column represents the party that the majority of people voted for in that state, that year, and the 'MajorityVote' column denotes the number of individuals that voted for the winning party in that state. 

In [2]:
election_results_1980_2008_path = "./data/Presedential election results reformatted.csv"
er_80_08 = pd.read_csv(election_results_1980_2008_path)
er_80_08.head()

State  Year Outcome  MajorityVote
0     Alabama  1980       R        654192
1      Alaska  1980       R         86112
2     Arizona  1980       R        529688
3    Arkansas  1980       R        403164
4  California  1980       R       4524858

In [3]:
election_results_2012_2016_path = "./data/Presdential Election 2012-2016 reformatted.csv"
er_12_16 = pd.read_csv(election_results_2012_2016_path)
er_12_16.head()

State  Year Outcome  MajorityVote
0     Alabama  2012       R       1255925
1      Alaska  2012       R        164676
2     Arizona  2012       R       1233654
3    Arkansas  2012       R        647744
4  California  2012       D       7854285

The following cell merges the two election result datasets, using the 'pd.concat' function.

In [4]:
us_er = pd.concat([er_80_08, er_12_16])
us_er.tail()

State  Year Outcome  MajorityVote
95       Virginia  2016       D       1981473
96     Washington  2016       D       1742718
97  West Virginia  2016       R        489371
98      Wisconsin  2016       R       1405284
99        Wyoming  2016       R        174419

The following cell indicates what the dual index looked like for the cleaned population dataset. This was useful for looking at specific years, states or indicators but unfortunately didn't allow for easy plotting or analysis, as Python doesn't do well with manipulating data that has 2 columns set as the indext. Also the 'astype.float' function converts the data in the MjorityVote column from a string value to a decimal number, as this will allow us to perform necessary arithetic functions with the data in the column later on. 

In [5]:
us_er = us_er.set_index(['State', 'Year'])
us_er = us_er.sort_index()
us_er['MajorityVote'] = us_er['MajorityVote'].astype(float)
us_er.head()

Outcome  MajorityVote
State   Year                      
Alabama 1980       R      654192.0
        1984       R      872849.0
        1988       R      815576.0
        1992       R      804283.0
        1996       R      749044.0

As explained above the dual column index won't allow us to do much with the data so we're first going to have to reset the index of the election result dataframe

In [6]:

us_er = us_er.reset_index()


##  Merging the population data with the election data and creating the political alignment index

Now we need to import the population data. The csv file that is being imported has already had its index reset like the above example. A new column called 'Unnamed: 0' with a repeat of the row number has been created in the process so it will be deleted using the '.drop' function. 

In [7]:
us_state_pop_path = "./data/us_state_pop__for_analysis.csv"

us_state_pop = pd.read_csv(us_state_pop_path)
us_state_pop.drop(['Unnamed: 0'], axis = 1, inplace = True)

us_state_pop.head()

State  Year  Population
0  Alabama  1970   3444354.0
1  Alabama  1971   3497000.0
2  Alabama  1972   3540000.0
3  Alabama  1973   3581000.0
4  Alabama  1974   3628000.0

To calculate the average political alignment of voters in each state each year, we first need to calculate the proportion of the population that voted for the most popular party in each state and year. To do this, the population data needs to be added for the relevant years to the election results dataframe. This requires setting a new index called 'StateYear' that merges the 'State' and 'Year' column in the population dataframe (shown in the first 3 rows of code in the cell below). As the data is asymmetrical, ideally we don't want a left, right or inner join and the outer join function didn't prove very effective for handling this dataset. Therefore, we found a function '.iterrows', which iterates through the rows and only adds the population data to the election result dataframe if it finds the relevant state-year combination in the population dataframe. The for loop allows the function to be repeated for all rows of the dataframe individually. The propotion of the population that voted for the state's most popular party can then be calculated by dividing the 'MajorityVote' column by the 'Population' column. 

Now the average political alignmnent (represented in the 'Alignment' column) can be calculated. This makes use of a similar 'for loop' and '.iterrow' combination. That loop basically tells it to iterrate through the rows and if it finds that the outcome was democrat (D) that year for that state, then multiply the proportion by -1, and if it was republican then the Alignment value is the same as the proportion value for that state and year. This allows us to categorise voting behaviour on a well defined range, from very democrat (-1) to very republican (+1). 

In [8]:
for row in us_state_pop:
    us_state_pop['StateYear']= us_state_pop['State'] + us_state_pop['Year'].map(str)

us_state_pop = us_state_pop.set_index(['StateYear'])

for x,row in us_er.iterrows():
    election_state_year = us_er['State'] + us_er['Year'].map(str)
    us_er['Population'] = us_state_pop.loc[election_state_year, 'Population'].values
us_er.head()

State  Year Outcome  MajorityVote  Population
0  Alabama  1980       R      654192.0   3893888.0
1  Alabama  1984       R      872849.0   3951820.0
2  Alabama  1988       R      815576.0   4023844.0
3  Alabama  1992       R      804283.0   4154014.0
4  Alabama  1996       R      749044.0   4331102.0

In [9]:
us_er['Proportion'] = us_er['MajorityVote']/us_er['Population']
us_er['Alignment'] = us_er['Proportion'].apply(abs)

for x, row in us_er.iterrows():
    if row['Outcome'] == 'R': 
        us_er.loc[x,'Alignment']=us_er.loc[x,'Proportion']
    elif row['Outcome'] == 'D':
        us_er.loc[x,'Alignment']=us_er.loc[x,'Proportion']*(-1)
us_er

State  Year Outcome  MajorityVote  Population  Proportion  \
0          Alabama  1980       R      654192.0   3893888.0    0.168005   
1          Alabama  1984       R      872849.0   3951820.0    0.220873   
2          Alabama  1988       R      815576.0   4023844.0    0.202686   
3          Alabama  1992       R      804283.0   4154014.0    0.193616   
4          Alabama  1996       R      749044.0   4331102.0    0.172945   
5          Alabama  2000       R      941173.0   4452173.0    0.211396   
6          Alabama  2004       D     1176394.0   4530729.0    0.259648   
7          Alabama  2008       D     1266546.0   4718206.0    0.268438   
8          Alabama  2012       R     1255925.0   4815960.0    0.260784   
9          Alabama  2016       R     1318255.0   4863300.0    0.271062   
10          Alaska  1980       R       86112.0    401851.0    0.214288   
11          Alaska  1984       R      138377.0    513702.0    0.269372   
12          Alaska  1988       R      119251.0    541983.0    0.220027   
13          Alaska  1992       R      102000.0    588736.0    0.173253   
14          Alaska  1996       R      122380.0    608569.0    0.201095   
15          Alaska  2000       R      167398.0    627963.0    0.266573   
16          Alaska  2004       D      190889.0    659286.0    0.289539   
17          Alaska  2008       D      193841.0    687455.0    0.281969   
18          Alaska  2012       R      164676.0    731089.0    0.225248   
19          Alaska  2016       R      163387.0    741894.0    0.220230   
20         Arizona  1980       R      529688.0   2718215.0    0.194866   
21         Arizona  1984       R      681416.0   3067135.0    0.222167   
22         Arizona  1988       R      702541.0   3535183.0    0.198728   
23         Arizona  1992       R      572086.0   3915740.0    0.146099   
24         Arizona  1996       R      653288.0   4586940.0    0.142423   
25         Arizona  2000       R      781652.0   5160586.0    0.151466   
26         Arizona  2004       D     1104294.0   5652404.0    0.195367   
27         Arizona  2008       D     1230111.0   6280362.0    0.195866   
28         Arizona  2012       R     1233654.0   6549634.0    0.188355   
29         Arizona  2016       R     1252401.0   6931071.0    0.180694   
..             ...   ...     ...           ...         ...         ...   
470  West Virginia  1980       D      367462.0   1949644.0    0.188476   
471  West Virginia  1984       R      405483.0   1927697.0    0.210346   
472  West Virginia  1988       D      341016.0   1830215.0    0.186326   
473  West Virginia  1992       D      331001.0   1806451.0    0.183233   
474  West Virginia  1996       D      327812.0   1822808.0    0.179839   
475  West Virginia  2000       R      336475.0   1807021.0    0.186204   
476  West Virginia  2004       D      423778.0   1816438.0    0.233302   
477  West Virginia  2008       D      393466.0   1840310.0    0.213804   
478  West Virginia  2012       R      417655.0   1856560.0    0.224962   
479  West Virginia  2016       R      489371.0   1831102.0    0.267255   
480      Wisconsin  1980       R     1088845.0   4705767.0    0.231385   
481      Wisconsin  1984       R     1198584.0   4735563.0    0.253103   
482      Wisconsin  1988       D     1126794.0   4822388.0    0.233659   
483      Wisconsin  1992       D     1041066.0   5025398.0    0.207161   
484      Wisconsin  1996       D     1071971.0   5229986.0    0.204966   
485      Wisconsin  2000       D     1242987.0   5373999.0    0.231296   
486      Wisconsin  2004       R     1489504.0   5514026.0    0.270130   
487      Wisconsin  2008       R     1677211.0   5640996.0    0.297325   
488      Wisconsin  2012       D     1620985.0   5726177.0    0.283083   
489      Wisconsin  2016       R     1405284.0   5778708.0    0.243183   
490        Wyoming  1980       R      110700.0    469557.0    0.235754   
491        Wyoming  1984       R      133241.0    504896.0    0.263898   
492        Wyomin

This has worked great but we want to have election data from every year so we can more easily analyse the relationship between voting behaviour and the different environmental indicators later on. Therefore, we will assume that the voting behaviour doesn't change in between election years (i.e. if a state voted republican in 2004, we will assume that the voting behaviour in that state will be the same in 2005, 2006 and 2007). 

To do this, inserting blank rows is not only hard, but also inefficient, so we will merge the new election result dataframe with the popualtion dataframe, as this has yearly data, thus allowing us to complete the election results for each year that presedential elections didn't occur. This can be done using the same princple of the 'for loop' and '.iterrow' combination but in the opposite way from what was done above: 
Python will iterrate through all the rows of the population dataframe and when there is a match between the election result 'StateYear' and the population 'StateYear', the election result data will be added to the relevant row in the population dataframe. After this, the relevant election result data will be copied for the missing years, using the '.fillna(method='ffill')' function. This function basically assumes the closest value in the column directly above it for empty cells in the dataframe. 

In [10]:
for row in us_er:
    us_er['StateYear']= us_er['State'] + us_er['Year'].map(str)

us_er = us_er.set_index(['StateYear'])

for x,row in us_state_pop.iterrows():
    election_state_year = us_state_pop['State'] + us_state_pop['Year'].map(str)
    us_state_pop['Alignment'] = us_er.loc[election_state_year, 'Alignment'].values
    us_state_pop['Outcome'] = us_er.loc[election_state_year, 'Outcome']
us_state_pop.head()

State  Year  Population  Alignment Outcome
StateYear                                                
Alabama1970  Alabama  1970   3444354.0        NaN     NaN
Alabama1971  Alabama  1971   3497000.0        NaN     NaN
Alabama1972  Alabama  1972   3540000.0        NaN     NaN
Alabama1973  Alabama  1973   3581000.0        NaN     NaN
Alabama1974  Alabama  1974   3628000.0        NaN     NaN

In [11]:
us_state_pop = us_state_pop.fillna(method='ffill')
us_state_pop

State  Year  Population  Alignment Outcome
StateYear                                                
Alabama1970  Alabama  1970   3444354.0        NaN     NaN
Alabama1971  Alabama  1971   3497000.0        NaN     NaN
Alabama1972  Alabama  1972   3540000.0        NaN     NaN
Alabama1973  Alabama  1973   3581000.0        NaN     NaN
Alabama1974  Alabama  1974   3628000.0        NaN     NaN
Alabama1975  Alabama  1975   3680000.0        NaN     NaN
Alabama1976  Alabama  1976   3737000.0        NaN     NaN
Alabama1977  Alabama  1977   3783000.0        NaN     NaN
Alabama1978  Alabama  1978   3834000.0        NaN     NaN
Alabama1979  Alabama  1979   3869000.0        NaN     NaN
Alabama1980  Alabama  1980   3893888.0   0.168005       R
Alabama1981  Alabama  1981   3918531.0   0.168005       R
Alabama1982  Alabama  1982   3925266.0   0.168005       R
Alabama1983  Alabama  1983   3934102.0   0.168005       R
Alabama1984  Alabama  1984   3951820.0   0.220873       R
Alabama1985  Alabama  1985   3972523.0   0.220873       R
Alabama1986  Alabama  1986   3991569.0   0.220873       R
Alabama1987  Alabama  1987   4015264.0   0.220873       R
Alabama1988  Alabama  1988   4023844.0   0.202686       R
Alabama1989  Alabama  1989   4030222.0   0.202686       R
Alabama1990  Alabama  1990   4050055.0   0.202686       R
Alabama1991  Alabama  1991   4099156.0   0.202686       R
Alabama1992  Alabama  1992   4154014.0   0.193616       R
Alabama1993  Alabama  1993   4214202.0   0.193616       R
Alabama1994  Alabama  1994   4260229.0   0.193616       R
Alabama1995  Alabama  1995   4296800.0   0.193616       R
Alabama1996  Alabama  1996   4331102.0   0.172945       R
Alabama1997  Alabama  1997   4367935.0   0.172945       R
Alabama1998  Alabama  1998   4404701.0   0.172945       R
Alabama1999  Alabama  1999   4430141.0   0.172945       R
...              ...   ...         ...        ...     ...
Wyoming1987  Wyoming  1987    476965.0   0.263898       R
Wyoming1988  Wyoming  1988    465101.0   0.229772       R
Wyoming1989  Wyoming  1989    458374.0   0.229772       R
Wyoming1990  Wyoming  1990    453690.0   0.229772       R
Wyoming1991  Wyoming  1991    459260.0   0.229772       R
Wyoming1992  Wyoming  1992    466251.0   0.170181       R
Wyoming1993  Wyoming  1993    473081.0   0.170181       R
Wyoming1994  Wyoming  1994    480283.0   0.170181       R
Wyoming1995  Wyoming  1995    485160.0   0.170181       R
Wyoming1996  Wyoming  1996    488167.0   0.215885       R
Wyoming1997  Wyoming  1997    489451.0   0.215885       R
Wyoming1998  Wyoming  1998    490787.0   0.215885       R
Wyoming1999  Wyoming  1999    491780.0   0.215885       R
Wyoming2000  Wyoming  2000    494300.0   0.298754       R
Wyoming2001  Wyoming  2001    494657.0   0.298754       R
Wyoming2002  Wyoming  2002    500017.0   0.298754       R
Wyoming2003  Wyoming  2003    503453.0   0.298754       R
Wyoming2004  Wyoming  2004    509106.0  -0.329261       D
Wyoming2005  Wyoming  2005    514157.0  -0.329261       D
Wyoming2006  Wyoming  2006    522667.0  -0.329261       D
Wyoming2007  Wyoming  2007    534876.0  -0.329261       D
Wyoming2008  Wyoming  2008    546043.0  -0.283784       D
Wyoming2009  Wyoming  2009    559851.0  -0.283784       D
Wyoming2010  Wyoming  2010    564513.0  -0.283784       D
Wyoming2011  Wyoming  2011    567725.0  -0.283784       D
Wyoming2012  Wyoming  2012    576765.0   0.296415       R
Wyoming2013  Wyoming  2013    582684.0   0.296415       R
Wyoming2014  Wyoming  2014    583642.0   0.296415       R
Wyoming2015  Wyoming  2015    586555.0   0.296415       R
Wyoming2016  Wyoming  2016    585501.0   0.297897       R

[2350 rows x 5 columns]

## Adding the different environmental indicator data to the election result-population dataframe

All of the data will now be merged into one dataframe, as this will make susbsequent data analysis and plotting easier. The per capita water consumption, total carbon dioxide (co2) emissions, renewable energy consumption in the residential sector (RETCB), total energy consumption (TERPB), and total petroleum product consumption (PARCP) will now be added. The co2 emission data, RETCB and PARCP data was not per capita, so this was made per capita by dividing their values by the population columns. 

In [12]:
state_water_use_path = "./data/state_water_use_copy1.csv"
state_water_use = pd.read_csv(state_water_use_path)
state_water_use.head()

Unnamed: 0    State  Year  \
0           0  Alabama  1990   
1           1  Alabama  1995   
2           2  Alabama  2000   
3           3  Alabama  2005   
4           4  Alabama  2010   

   Domestic self-supplied groundwater withdrawals, fresh, in Mgal/d  \
0                                              27.74                  
1                                              61.90                  
2                                              65.06                  
3                                              39.12                  
4                                              37.97                  

   Domestic self-supplied groundwater withdrawals, saline, in Mgal/d  \
0                                                0.0                   
1                                                0.0                   
2                                                0.0                   
3                                                0.0                   
4                                                0.0                   

   Domestic total self-supplied withdrawals, groundwater, in Mgal/d  \
0                                                0.0                  
1                                               61.9                  
2                                                0.0                  
3                                                0.0                  
4                                                0.0                  

   Domestic self-supplied surface-water withdrawals, fresh, in Mgal/d  \
0                                                0.0                    
1                                                0.0                    
2                                                0.0                    
3                                                0.0                    
4                                                0.0                    

   Domestic self-supplied surface-water withdrawals, saline, in Mgal/d  \
0                                                0.0                     
1                                                0.0                     
2                                                0.0                     
3                                                0.0                     
4                                                0.0                     

   Domestic total self-supplied withdrawals, surface water, in Mgal/d  \
0                                                0.0                    
1                                                0.0                    
2                                                0.0                    
3                                                0.0                    
4                                                0.0                    

   Domestic total self-supplied withdrawals, fresh, in Mgal/d  \
0                                              27.74            
1                                              61.90            
2                                              65.06            
3                                              39.12            
4                                              37.97            

                            ...                             \
0                           ...                              
1                           ...                              
2                           ...                              
3                           ...                              
4                           ...                              

   Domestic deliveries from public supply, in Mgal/d  \
0                                             368.47   
1                                             383.31   
2                                               0.00   
3                                             325.94   
4                                             326.69   

   Domestic total self-supplied withdrawals, saline, in Mgal/d  \
0                                

In [13]:
for row in state_water_use:
    state_water_use['StateYear']= state_water_use['State'] + state_water_use['Year'].map(str)

state_water_use = state_water_use.set_index(['StateYear'])

for x,row in us_state_pop.iterrows():
    election_state_year = us_state_pop['State'] + us_state_pop['Year'].map(str)
    us_state_pop['Total domestic water use per capita, gallons/person/day'] = state_water_use.loc[election_state_year, 'Total domestic water use per capita, gallons/person/day'].values
pd.options.display.max_rows = 5000

us_state_pop.head()

State  Year  Population  Alignment Outcome  \
StateYear                                                   
Alabama1970  Alabama  1970   3444354.0        NaN     NaN   
Alabama1971  Alabama  1971   3497000.0        NaN     NaN   
Alabama1972  Alabama  1972   3540000.0        NaN     NaN   
Alabama1973  Alabama  1973   3581000.0        NaN     NaN   
Alabama1974  Alabama  1974   3628000.0        NaN     NaN   

             Total domestic water use per capita, gallons/person/day  
StateYear                                                             
Alabama1970                                                NaN        
Alabama1971                                                NaN        
Alabama1972                                                NaN        
Alabama1973                                                NaN        
Alabama1974                                                NaN

In [14]:
co2_emissions_path = "./data/co2_emissions_copy_use.csv"
co2_emissions = pd.read_csv(co2_emissions_path)
co2_emissions.head()

State  Year  Reading
0  Alabama  1980      3.6
1  Alabama  1981      3.4
2  Alabama  1982      3.4
3  Alabama  1983      3.5
4  Alabama  1984      3.3

In [15]:
for row in co2_emissions:
    co2_emissions['StateYear']= co2_emissions['State'] + co2_emissions['Year'].map(str)

co2_emissions = co2_emissions.set_index(['StateYear'])

for x,row in us_state_pop.iterrows():
    election_state_year = us_state_pop['State'] + us_state_pop['Year'].map(str)
    us_state_pop['Residential co2 emissions, million metric tons'] = co2_emissions.loc[election_state_year, 'Reading'].values

us_state_pop

State  Year  Population  Alignment Outcome  \
StateYear                                                                 
Alabama1970                Alabama  1970   3444354.0        NaN     NaN   
Alabama1971                Alabama  1971   3497000.0        NaN     NaN   
Alabama1972                Alabama  1972   3540000.0        NaN     NaN   
Alabama1973                Alabama  1973   3581000.0        NaN     NaN   
Alabama1974                Alabama  1974   3628000.0        NaN     NaN   
Alabama1975                Alabama  1975   3680000.0        NaN     NaN   
Alabama1976                Alabama  1976   3737000.0        NaN     NaN   
Alabama1977                Alabama  1977   3783000.0        NaN     NaN   
Alabama1978                Alabama  1978   3834000.0        NaN     NaN   
Alabama1979                Alabama  1979   3869000.0        NaN     NaN   
Alabama1980                Alabama  1980   3893888.0   0.168005       R   
Alabama1981                Alabama  1981   3918531.0   0.168005       R   
Alabama1982                Alabama  1982   3925266.0   0.168005       R   
Alabama1983                Alabama  1983   3934102.0   0.168005       R   
Alabama1984                Alabama  1984   3951820.0   0.220873       R   
Alabama1985                Alabama  1985   3972523.0   0.220873       R   
Alabama1986                Alabama  1986   3991569.0   0.220873       R   
Alabama1987                Alabama  1987   4015264.0   0.220873       R   
Alabama1988                Alabama  1988   4023844.0   0.202686       R   
Alabama1989                Alabama  1989   4030222.0   0.202686       R   
Alabama1990                Alabama  1990   4050055.0   0.202686       R   
Alabama1991                Alabama  1991   4099156.0   0.202686       R   
Alabama1992                Alabama  1992   4154014.0   0.193616       R   
Alabama1993                Alabama  1993   4214202.0   0.193616       R   
Alabama1994                Alabama  1994   4260229.0   0.193616       R   
Alabama1995                Alabama  1995   4296800.0   0.193616       R   
Alabama1996                Alabama  1996   4331102.0   0.172945       R   
Alabama1997                Alabama  1997   4367935.0   0.172945       R   
Alabama1998                Alabama  1998   4404701.0   0.172945       R   
Alabama1999                Alabama  1999   4430141.0   0.172945       R   
Alabama2000                Alabama  2000   4452173.0   0.211396       R   
Alabama2001                Alabama  2001   4467634.0   0.211396       R   
Alabama2002                Alabama  2002   4480089.0   0.211396       R   
Alabama2003                Alabama  2003   4503491.0   0.211396       R   
Alabama2004                Alabama  2004   4530729.0  -0.259648       D   
Alabama2005                Alabama  2005   4569805.0  -0.259648       D   
Alabama2006                Alabama  2006   4628981.0  -0.259648       D   
Alabama2007                Alabama  2007   4672840.0  -0.259648       D   
Alabama2008                Alabama  2008   4718206.0  -0.268438       D   
Alabama2009                Alabama  2009   4757938.0  -0.268438       D   
Alabama2010                Alabama  2010   4785492.0  -0.268438       D   
Alabama2011                Alabama  2011   4799918.0  -0.268438       D   
Alabama2012                Alabama  2012   4815960.0   0.260784       R   
Alabama2013                Alabama  2013   4829479.0   0.260784       R   
Alabama2014                Alabama  2014   4843214.0   0.260784       R   
Alabama2015                Alabama  2015   4853875.0   0.260784       R   
Alabama2016                Alabama  2016   4863300.0   0.271062       R   
Alaska1970                  Alaska  1970    302583.0   0.271062       R   
Alaska1971                  Alaska  1971    316000.0   0.271062       R   
Alaska1972                  Alaska  1972    326000.0   0.271062       R   
Alaska1973                  Alaska  1973    333000.0   0.271062       R   
Alaska1974                  Alaska  1974    345000.0  

In [16]:
us_state_pop['Residential co2 emissions, metric tons/person'] = us_state_pop['Residential co2 emissions, million metric tons']*1000000/us_state_pop['Population']
us_state_pop.head()

State  Year  Population  Alignment Outcome  \
StateYear                                                   
Alabama1970  Alabama  1970   3444354.0        NaN     NaN   
Alabama1971  Alabama  1971   3497000.0        NaN     NaN   
Alabama1972  Alabama  1972   3540000.0        NaN     NaN   
Alabama1973  Alabama  1973   3581000.0        NaN     NaN   
Alabama1974  Alabama  1974   3628000.0        NaN     NaN   

             Total domestic water use per capita, gallons/person/day  \
StateYear                                                              
Alabama1970                                                NaN         
Alabama1971                                                NaN         
Alabama1972                                                NaN         
Alabama1973                                                NaN         
Alabama1974                                                NaN         

             Residential co2 emissions, million metric tons  \
StateYear                                                     
Alabama1970                                             NaN   
Alabama1971                                             NaN   
Alabama1972                                             NaN   
Alabama1973                                             NaN   
Alabama1974                                             NaN   

             Residential co2 emissions, metric tons/person  
StateYear                                                   
Alabama1970                                            NaN  
Alabama1971                                            NaN  
Alabama1972                                            NaN  
Alabama1973                                            NaN  
Alabama1974                                            NaN

In [17]:
consumption_btu_csv_path = "./data/consumption_btu_actual_done.csv"
consumption_btu = pd.read_csv(consumption_btu_csv_path)
consumption_btu



Unnamed: 0           State    MSN  Year      Reading
0                0          Alaska  ABICB  1970         0.00
1                1          Alaska  ARICB  1970      1817.00
2                2          Alaska  ARTCB  1970      1817.00
3                3          Alaska  ARTXB  1970      1817.00
4                4          Alaska  AVACB  1970      2331.00
5                5          Alaska  AVTCB  1970      2331.00
6                6          Alaska  AVTXB  1970      2331.00
7                7          Alaska  BMTCB  1970      5029.00
8                8          Alaska  CLACB  1970        14.00
9                9          Alaska  CLCCB  1970       183.00
10              10          Alaska  CLEIB  1970      4254.00
11              11          Alaska  CLICB  1970      8476.00
12              12          Alaska  CLKCB  1970         0.00
13              13          Alaska  CLOCB  1970      8476.00
14              14          Alaska  CLRCB  1970       233.00
15              15          Alaska  CLTCB  1970     13159.00
16              16          Alaska  CLTXB  1970      8905.00
17              17          Alaska  COICB  1970         0.00
18              18          Alaska  DFACB  1970      5823.00
19              19          Alaska  DFCCB  1970      2456.00
20              20          Alaska  DFEIB  1970      2296.00
21              21          Alaska  DFICB  1970     11202.00
22              22          Alaska  DFRCB  1970      7932.00
23              23          Alaska  DFTCB  1970     29710.00
24              24          Alaska  DFTXB  1970     27413.00
25              25          Alaska  DKEIB  1970      2296.00
26              26          Alaska  ELEXB  1970         0.00
27              27          Alaska  ELIMB  1970         0.00
28              28          Alaska  ELISB  1970         0.00
29              29          Alaska  ELNIB  1970         0.00
30              30          Alaska  EMACB  1970         0.00
31              31          Alaska  EMCCB  1970         0.00
32              32          Alaska  EMICB  1970         0.00
33              33          Alaska  EMLCB  1970         0.00
34              34          Alaska  EMTCB  1970         0.00
35              35          Alaska  ESACB  1970         0.00
36              36          Alaska  ESCCB  1970      1632.00
37              37          Alaska  ESICB  1970       345.00
38              38          Alaska  ESRCB  1970      1798.00
39              39          Alaska  ESTCB  1970      3774.00
40              40          Alaska  ESTXB  1970      3774.00
41              41          Alaska  FFTCB  1970    173208.00
42              42          Alaska  FNICB  1970         0.00
43              43          Alaska  FOICB  1970         0.00
44              44          Alaska  FSICB  1970       223.00
45              45          Alaska  GDPRX  1970          NaN
46              46          Alaska  GECCB  1970         0.00
47              47          Alaska  GEEGB  1970         0.00
48              48          Alaska  GEICB  1970         0.00
49              49          Alaska  GERCB  1970         0.00
50              50          Alaska  GETCB  1970         0.00
51              51          Alaska  GETXB  1970         0.00
52              52          Alaska  HYCCB  1970         0.00
53              53          Alaska  HYEGB  1970      3806.00
54              54          Alaska  HYICB  1970         0.00
55              55          Alaska  HYTCB  1970      3806.00
56              56          Alaska  HYTXB  1970         0.00
57              57          Alaska  JFACB  1970     37702.00
58              58          Alaska  JFTCB  1970     37702.00
59              59          Alaska  JFTXB  1970     37702.00
60              60          Alaska  JKACB  1970     29452.00
61              61          Alaska  JKTCB  1970     29452.00
62              62          Alaska  JNACB  1970      8250.00
63              63          Alaska  JNTCB  1970      8250.00
64              64          Alaska  KSCCB  

In [18]:
value_list_btu_RETCB = ['RETCB']

consumption_btu_RETCB = consumption_btu[consumption_btu.MSN.isin(value_list_btu_RETCB)]
consumption_btu_RETCB.head()

Unnamed: 0       State    MSN  Year   Reading
132         132      Alaska  RETCB  1970    8835.0
323         323     Alabama  RETCB  1970  132471.0
514         514    Arkansas  RETCB  1970   56933.0
705         705     Arizona  RETCB  1970   68919.0
896         896  California  RETCB  1970  521978.0

In [19]:
for row in consumption_btu_RETCB:
    consumption_btu_RETCB['StateYear']= consumption_btu_RETCB['State'] + consumption_btu_RETCB['Year'].map(str)

consumption_btu_RETCB = consumption_btu_RETCB.set_index(['StateYear'])

for x,row in us_state_pop.iterrows():
    election_state_year = us_state_pop['State'] + us_state_pop['Year'].map(str)
    us_state_pop['Renewable energy total consumption, billion btu'] = consumption_btu_RETCB.loc[election_state_year, 'Reading'].values

us_state_pop.head()

/home/nbuser/anaconda3_501/lib/python3.6/site-packages/ipykernel/__main__.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  from ipykernel import kernelapp as app


State  Year  Population  Alignment Outcome  \
StateYear                                                   
Alabama1970  Alabama  1970   3444354.0        NaN     NaN   
Alabama1971  Alabama  1971   3497000.0        NaN     NaN   
Alabama1972  Alabama  1972   3540000.0        NaN     NaN   
Alabama1973  Alabama  1973   3581000.0        NaN     NaN   
Alabama1974  Alabama  1974   3628000.0        NaN     NaN   

             Total domestic water use per capita, gallons/person/day  \
StateYear                                                              
Alabama1970                                                NaN         
Alabama1971                                                NaN         
Alabama1972                                                NaN         
Alabama1973                                                NaN         
Alabama1974                                                NaN         

             Residential co2 emissions, million metric tons  \
StateYear                                                     
Alabama1970                                             NaN   
Alabama1971                                             NaN   
Alabama1972                                             NaN   
Alabama1973                                             NaN   
Alabama1974                                             NaN   

             Residential co2 emissions, metric tons/person  \
StateYear                                                    
Alabama1970                                            NaN   
Alabama1971                                            NaN   
Alabama1972                                            NaN   
Alabama1973                                            NaN   
Alabama1974                                            NaN   

             Renewable energy total consumption, billion btu  
StateYear                                                     
Alabama1970                                         132471.0  
Alabama1971                                         158182.0  
Alabama1972                                         164946.0  
Alabama1973                                         181706.0  
Alabama1974                                         166734.0

In [20]:
us_state_pop['Renewable energy total consumption, billion btu/person'] = us_state_pop['Renewable energy total consumption, billion btu']/us_state_pop['Population']
us_state_pop

State  Year  Population  Alignment Outcome  \
StateYear                                                                 
Alabama1970                Alabama  1970   3444354.0        NaN     NaN   
Alabama1971                Alabama  1971   3497000.0        NaN     NaN   
Alabama1972                Alabama  1972   3540000.0        NaN     NaN   
Alabama1973                Alabama  1973   3581000.0        NaN     NaN   
Alabama1974                Alabama  1974   3628000.0        NaN     NaN   
Alabama1975                Alabama  1975   3680000.0        NaN     NaN   
Alabama1976                Alabama  1976   3737000.0        NaN     NaN   
Alabama1977                Alabama  1977   3783000.0        NaN     NaN   
Alabama1978                Alabama  1978   3834000.0        NaN     NaN   
Alabama1979                Alabama  1979   3869000.0        NaN     NaN   
Alabama1980                Alabama  1980   3893888.0   0.168005       R   
Alabama1981                Alabama  1981   3918531.0   0.168005       R   
Alabama1982                Alabama  1982   3925266.0   0.168005       R   
Alabama1983                Alabama  1983   3934102.0   0.168005       R   
Alabama1984                Alabama  1984   3951820.0   0.220873       R   
Alabama1985                Alabama  1985   3972523.0   0.220873       R   
Alabama1986                Alabama  1986   3991569.0   0.220873       R   
Alabama1987                Alabama  1987   4015264.0   0.220873       R   
Alabama1988                Alabama  1988   4023844.0   0.202686       R   
Alabama1989                Alabama  1989   4030222.0   0.202686       R   
Alabama1990                Alabama  1990   4050055.0   0.202686       R   
Alabama1991                Alabama  1991   4099156.0   0.202686       R   
Alabama1992                Alabama  1992   4154014.0   0.193616       R   
Alabama1993                Alabama  1993   4214202.0   0.193616       R   
Alabama1994                Alabama  1994   4260229.0   0.193616       R   
Alabama1995                Alabama  1995   4296800.0   0.193616       R   
Alabama1996                Alabama  1996   4331102.0   0.172945       R   
Alabama1997                Alabama  1997   4367935.0   0.172945       R   
Alabama1998                Alabama  1998   4404701.0   0.172945       R   
Alabama1999                Alabama  1999   4430141.0   0.172945       R   
Alabama2000                Alabama  2000   4452173.0   0.211396       R   
Alabama2001                Alabama  2001   4467634.0   0.211396       R   
Alabama2002                Alabama  2002   4480089.0   0.211396       R   
Alabama2003                Alabama  2003   4503491.0   0.211396       R   
Alabama2004                Alabama  2004   4530729.0  -0.259648       D   
Alabama2005                Alabama  2005   4569805.0  -0.259648       D   
Alabama2006                Alabama  2006   4628981.0  -0.259648       D   
Alabama2007                Alabama  2007   4672840.0  -0.259648       D   
Alabama2008                Alabama  2008   4718206.0  -0.268438       D   
Alabama2009                Alabama  2009   4757938.0  -0.268438       D   
Alabama2010                Alabama  2010   4785492.0  -0.268438       D   
Alabama2011                Alabama  2011   4799918.0  -0.268438       D   
Alabama2012                Alabama  2012   4815960.0   0.260784       R   
Alabama2013                Alabama  2013   4829479.0   0.260784       R   
Alabama2014                Alabama  2014   4843214.0   0.260784       R   
Alabama2015                Alabama  2015   4853875.0   0.260784       R   
Alabama2016                Alabama  2016   4863300.0   0.271062       R   
Alaska1970                  Alaska  1970    302583.0   0.271062       R   
Alaska1971                  Alaska  1971    316000.0   0.271062       R   
Alaska1972                  Alaska  1972    326000.0   0.271062       R   
Alaska1973                  Alaska  1973    333000.0   0.271062       R   
Alaska1974                  Alaska  1974    345000.0  

In [21]:
value_list_btu_TERPB = ['TERPB']

consumption_btu_TERPB = consumption_btu[consumption_btu.MSN.isin(value_list_btu_TERPB)]
consumption_btu_TERPB.head()

Unnamed: 0       State    MSN  Year  Reading
160         160      Alaska  TERPB  1970     82.0
351         351     Alabama  TERPB  1970     64.0
542         542    Arkansas  TERPB  1970     75.0
733         733     Arizona  TERPB  1970     50.0
924         924  California  TERPB  1970     52.0

In [22]:
for row in consumption_btu_TERPB:
    consumption_btu_TERPB['StateYear']= consumption_btu_TERPB['State'] + consumption_btu_TERPB['Year'].map(str)

consumption_btu_TERPB = consumption_btu_TERPB.set_index(['StateYear'])

for x,row in us_state_pop.iterrows():
    election_state_year = us_state_pop['State'] + us_state_pop['Year'].map(str)
    us_state_pop['Total energy consumption per capita in the residential sector, Million Btu/person'] = consumption_btu_TERPB.loc[election_state_year, 'Reading'].values

us_state_pop.head()

/home/nbuser/anaconda3_501/lib/python3.6/site-packages/ipykernel/__main__.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  from ipykernel import kernelapp as app


State  Year  Population  Alignment Outcome  \
StateYear                                                   
Alabama1970  Alabama  1970   3444354.0        NaN     NaN   
Alabama1971  Alabama  1971   3497000.0        NaN     NaN   
Alabama1972  Alabama  1972   3540000.0        NaN     NaN   
Alabama1973  Alabama  1973   3581000.0        NaN     NaN   
Alabama1974  Alabama  1974   3628000.0        NaN     NaN   

             Total domestic water use per capita, gallons/person/day  \
StateYear                                                              
Alabama1970                                                NaN         
Alabama1971                                                NaN         
Alabama1972                                                NaN         
Alabama1973                                                NaN         
Alabama1974                                                NaN         

             Residential co2 emissions, million metric tons  \
StateYear                                                     
Alabama1970                                             NaN   
Alabama1971                                             NaN   
Alabama1972                                             NaN   
Alabama1973                                             NaN   
Alabama1974                                             NaN   

             Residential co2 emissions, metric tons/person  \
StateYear                                                    
Alabama1970                                            NaN   
Alabama1971                                            NaN   
Alabama1972                                            NaN   
Alabama1973                                            NaN   
Alabama1974                                            NaN   

             Renewable energy total consumption, billion btu  \
StateYear                                                      
Alabama1970                                         132471.0   
Alabama1971                                         158182.0   
Alabama1972                                         164946.0   
Alabama1973                                         181706.0   
Alabama1974                                         166734.0   

             Renewable energy total consumption, billion btu/person  \
StateYear                                                             
Alabama1970                                           0.038460        
Alabama1971                                           0.045234        
Alabama1972                                           0.046595        
Alabama1973                                           0.050742        
Alabama1974                                           0.045958        

             Total energy consumption per capita in the residential sector, Million Btu/person  
StateYear                                                                                       
Alabama1970                                               64.0                                  
Alabama1971                                               65.0                                  
Alabama1972                                               68.0                                  
Alabama1973                                               71.0                                  
Alabama1974                                               70.0

In [23]:
consumption_phy_csv_path = "./data/consumption_phy_done.csv"
consumption_phy = pd.read_csv(consumption_phy_csv_path)
consumption_phy.head()


Unnamed: 0   State    MSN  Year  Reading
0           0  Alaska  ABICP  1970      NaN
1           1  Alaska  ARICP  1970    274.0
2           2  Alaska  ARTCP  1970    274.0
3           3  Alaska  ARTXP  1970    274.0
4           4  Alaska  AVACP  1970    462.0

In [24]:
# PARCP is the all petroleum products consumed by the residential sector
value_list_PARCP = ['PARCP']

consumption_phy_PARCP = consumption_phy[consumption_phy.MSN.isin(value_list_PARCP)]
consumption_phy_PARCP

Unnamed: 0           State    MSN  Year  Reading
97              97          Alaska  PARCP  1970   1432.0
227            227         Alabama  PARCP  1970   4456.0
357            357        Arkansas  PARCP  1970   6491.0
487            487         Arizona  PARCP  1970    915.0
617            617      California  PARCP  1970   5182.0
747            747        Colorado  PARCP  1970   3353.0
877            877     Connecticut  PARCP  1970  15388.0
1007          1007        Delaware  PARCP  1970   2755.0
1137          1137         Florida  PARCP  1970   6306.0
1267          1267         Georgia  PARCP  1970   4085.0
1397          1397          Hawaii  PARCP  1970    200.0
1527          1527            Iowa  PARCP  1970   9784.0
1657          1657           Idaho  PARCP  1970   1447.0
1787          1787              IL  PARCP  1970  21962.0
1917          1917              IN  PARCP  1970  16339.0
2047          2047              KS  PARCP  1970   5221.0
2177          2177              KY  PARCP  1970   5884.0
2307          2307              LA  PARCP  1970   2318.0
2437          2437              MA  PARCP  1970  40748.0
2567          2567        Maryland  PARCP  1970  11214.0
2697          2697           Maine  PARCP  1970   9751.0
2827          2827        Michigan  PARCP  1970  24226.0
2957          2957       Minnesota  PARCP  1970  14955.0
3087          3087        Missouri  PARCP  1970   9769.0
3217          3217     Mississippi  PARCP  1970   4744.0
3347          3347         Montana  PARCP  1970   1106.0
3477          3477  North Carolina  PARCP  1970  21269.0
3607          3607    North Dakota  PARCP  1970   2555.0
3737          3737        Nebraska  PARCP  1970   4821.0
3867          3867   New Hampshire  PARCP  1970   7136.0
3997          3997      New Jersey  PARCP  1970  34448.0
4127          4127      New Mexico  PARCP  1970   1939.0
4257          4257          Nevada  PARCP  1970    836.0
4387          4387        New York  PARCP  1970  68259.0
4517          4517            Ohio  PARCP  1970  16136.0
4647          4647        Oklahoma  PARCP  1970   5802.0
4777          4777          Oregon  PARCP  1970   3850.0
4907          4907    Pennsylvania  PARCP  1970  36222.0
5037          5037    Rhode Island  PARCP  1970   6294.0
5167          5167  South Carolina  PARCP  1970   5814.0
5297          5297    South Dakota  PARCP  1970   2761.0
5427          5427       Tennessee  PARCP  1970   4382.0
5557          5557           Texas  PARCP  1970  14062.0
5687          5687            Utah  PARCP  1970    639.0
5817          5817        Virginia  PARCP  1970  15462.0
5947          5947         Vermont  PARCP  1970   4596.0
6077          6077      Washington  PARCP  1970   8214.0
6207          6207       Wisconsin  PARCP  1970  19198.0
6337          6337   West Virginia  PARCP  1970    772.0
6467          6467         Wyoming  PARCP  1970    874.0
6597          6597          Alaska  PARCP  1971   1869.0
6727          6727         Alabama  PARCP  1971   4674.0
6857          6857        Arkansas  PARCP  1971   6844.0
6987          6987         Arizona  PARCP  1971    928.0
7117          7117      California  PARCP  1971   5488.0
7247          7247        Colorado  PARCP  1971   3532.0
7377          7377     Connecticut  PARCP  1971  15086.0
7507          7507        Delaware  PARCP  1971   2763.0
7637          7637         Florida  PARCP  1971   6167.0
7767          7767         Georgia  PARCP  1971   4227.0
7897          7897          Hawaii  PARCP  1971    234.0
8027          8027            Iowa  PARCP  1971   9497.0
8157          8157           Idaho  PARCP  1971   1516.0
8287          8287              IL  PARCP  1971  22186.0
8417          8417              IN  PARCP  1971  16900.0
8547          8547              KS  PARCP  1971   4965.0
8677          8677              KY  PARCP  1971   5721.0
8807          8807              LA  PARCP  1971   2476.0
8937          8937              MA  PARCP  1971  42332.0
9067          9067

In [25]:
for row in consumption_phy_PARCP:
    consumption_phy_PARCP['StateYear']= consumption_phy_PARCP['State'] + consumption_phy_PARCP['Year'].map(str)

consumption_phy_PARCP = consumption_phy_PARCP.set_index(['StateYear'])

for x,row in us_state_pop.iterrows():
    election_state_year = us_state_pop['State'] + us_state_pop['Year'].map(str)
    us_state_pop['All petroleum products consumed by the residential sector, thousand barrels'] = consumption_phy_PARCP.loc[election_state_year, 'Reading'].values

us_state_pop.head()

/home/nbuser/anaconda3_501/lib/python3.6/site-packages/ipykernel/__main__.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  from ipykernel import kernelapp as app


State  Year  Population  Alignment Outcome  \
StateYear                                                   
Alabama1970  Alabama  1970   3444354.0        NaN     NaN   
Alabama1971  Alabama  1971   3497000.0        NaN     NaN   
Alabama1972  Alabama  1972   3540000.0        NaN     NaN   
Alabama1973  Alabama  1973   3581000.0        NaN     NaN   
Alabama1974  Alabama  1974   3628000.0        NaN     NaN   

             Total domestic water use per capita, gallons/person/day  \
StateYear                                                              
Alabama1970                                                NaN         
Alabama1971                                                NaN         
Alabama1972                                                NaN         
Alabama1973                                                NaN         
Alabama1974                                                NaN         

             Residential co2 emissions, million metric tons  \
StateYear                                                     
Alabama1970                                             NaN   
Alabama1971                                             NaN   
Alabama1972                                             NaN   
Alabama1973                                             NaN   
Alabama1974                                             NaN   

             Residential co2 emissions, metric tons/person  \
StateYear                                                    
Alabama1970                                            NaN   
Alabama1971                                            NaN   
Alabama1972                                            NaN   
Alabama1973                                            NaN   
Alabama1974                                            NaN   

             Renewable energy total consumption, billion btu  \
StateYear                                                      
Alabama1970                                         132471.0   
Alabama1971                                         158182.0   
Alabama1972                                         164946.0   
Alabama1973                                         181706.0   
Alabama1974                                         166734.0   

             Renewable energy total consumption, billion btu/person  \
StateYear                                                             
Alabama1970                                           0.038460        
Alabama1971                                           0.045234        
Alabama1972                                           0.046595        
Alabama1973                                           0.050742        
Alabama1974                                           0.045958        

             Total energy consumption per capita in the residential sector, Million Btu/person  \
StateYear                                                                                        
Alabama1970                                               64.0                                   
Alabama1971                                               65.0                                   
Alabama1972                                               68.0                                   
Alabama1973                                               71.0                                   
Alabama1974                                               70.0                                   

             All petroleum products consumed by the residential sector, thousand barrels  
StateYear                                                                                 
Alabama1970                                             4456.0                            
Alabama1971                                             4674.0                            
Alabama1972                                             5080.0                            
Alabama1973                                             4798.0                            
Alabama1974              

In [26]:
us_state_pop['All petroleum products consumed by the residential sector, thousand barrels/person'] = us_state_pop['All petroleum products consumed by the residential sector, thousand barrels']/us_state_pop['Population']
us_state_pop

State  Year  Population  Alignment Outcome  \
StateYear                                                                 
Alabama1970                Alabama  1970   3444354.0        NaN     NaN   
Alabama1971                Alabama  1971   3497000.0        NaN     NaN   
Alabama1972                Alabama  1972   3540000.0        NaN     NaN   
Alabama1973                Alabama  1973   3581000.0        NaN     NaN   
Alabama1974                Alabama  1974   3628000.0        NaN     NaN   
Alabama1975                Alabama  1975   3680000.0        NaN     NaN   
Alabama1976                Alabama  1976   3737000.0        NaN     NaN   
Alabama1977                Alabama  1977   3783000.0        NaN     NaN   
Alabama1978                Alabama  1978   3834000.0        NaN     NaN   
Alabama1979                Alabama  1979   3869000.0        NaN     NaN   
Alabama1980                Alabama  1980   3893888.0   0.168005       R   
Alabama1981                Alabama  1981   3918531.0   0.168005       R   
Alabama1982                Alabama  1982   3925266.0   0.168005       R   
Alabama1983                Alabama  1983   3934102.0   0.168005       R   
Alabama1984                Alabama  1984   3951820.0   0.220873       R   
Alabama1985                Alabama  1985   3972523.0   0.220873       R   
Alabama1986                Alabama  1986   3991569.0   0.220873       R   
Alabama1987                Alabama  1987   4015264.0   0.220873       R   
Alabama1988                Alabama  1988   4023844.0   0.202686       R   
Alabama1989                Alabama  1989   4030222.0   0.202686       R   
Alabama1990                Alabama  1990   4050055.0   0.202686       R   
Alabama1991                Alabama  1991   4099156.0   0.202686       R   
Alabama1992                Alabama  1992   4154014.0   0.193616       R   
Alabama1993                Alabama  1993   4214202.0   0.193616       R   
Alabama1994                Alabama  1994   4260229.0   0.193616       R   
Alabama1995                Alabama  1995   4296800.0   0.193616       R   
Alabama1996                Alabama  1996   4331102.0   0.172945       R   
Alabama1997                Alabama  1997   4367935.0   0.172945       R   
Alabama1998                Alabama  1998   4404701.0   0.172945       R   
Alabama1999                Alabama  1999   4430141.0   0.172945       R   
Alabama2000                Alabama  2000   4452173.0   0.211396       R   
Alabama2001                Alabama  2001   4467634.0   0.211396       R   
Alabama2002                Alabama  2002   4480089.0   0.211396       R   
Alabama2003                Alabama  2003   4503491.0   0.211396       R   
Alabama2004                Alabama  2004   4530729.0  -0.259648       D   
Alabama2005                Alabama  2005   4569805.0  -0.259648       D   
Alabama2006                Alabama  2006   4628981.0  -0.259648       D   
Alabama2007                Alabama  2007   4672840.0  -0.259648       D   
Alabama2008                Alabama  2008   4718206.0  -0.268438       D   
Alabama2009                Alabama  2009   4757938.0  -0.268438       D   
Alabama2010                Alabama  2010   4785492.0  -0.268438       D   
Alabama2011                Alabama  2011   4799918.0  -0.268438       D   
Alabama2012                Alabama  2012   4815960.0   0.260784       R   
Alabama2013                Alabama  2013   4829479.0   0.260784       R   
Alabama2014                Alabama  2014   4843214.0   0.260784       R   
Alabama2015                Alabama  2015   4853875.0   0.260784       R   
Alabama2016                Alabama  2016   4863300.0   0.271062       R   
Alaska1970                  Alaska  1970    302583.0   0.271062       R   
Alaska1971                  Alaska  1971    316000.0   0.271062       R   
Alaska1972                  Alaska  1972    326000.0   0.271062       R   
Alaska1973                  Alaska  1973    333000.0   0.271062       R   
Alaska1974                  Alaska  1974    345000.0  

In [90]:
us_state_pop_for_analysis_results_wbk_csv = us_state_pop.to_csv('./data/us_state_pop_for_analysis_results_wbk.csv')